<a href="https://colab.research.google.com/github/fur-elyse/clip-and-sub-youtube/blob/main/Download_Youtube_Videos.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install youtube-dl
!pip install ffmpeg-python

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 59.2 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
import re
import os
from datetime import datetime

import ffmpeg
from youtube_dl import YoutubeDL

# packages to play video on colab
from base64 import b64encode
from IPython.display import HTML

In [4]:
def get_youtube_url(url, content):

    youtube_dl_opts = {
        'format': f'best{content}', # choice of quality
        'quiet': True
    }

    with YoutubeDL(youtube_dl_opts) as ydl:
        video_info = ydl.extract_info(url, download=False)

    if content == "video":
        return video_info["url"], video_info["id"]
    return video_info["url"]


def convert_to_seconds(timestamp):
    
    # reformat timestamps so that they follow this format xx:xx:xx
    format = "%H:%M:%S" if len(timestamp) > 5 else "%M:%S"
    timestamp = datetime.strptime(timestamp, format).strftime("%H:%M:%S")

    hour, min, sec = timestamp.split(':')
    return int(hour) * 3600 + int(min) * 60 + int(sec)


def get_duration_in_seconds(timestamp):
    timestamp = timestamp.split("-")
    start_time = convert_to_seconds(timestamp[0])
    end_time = convert_to_seconds(timestamp[-1])
    return start_time, end_time - start_time


def download_video(video_url, audio_url, start_time, duration):
    video = ffmpeg.input(video_url, ss=start_time, t=duration).video
    audio = ffmpeg.input(audio_url, ss=start_time, t=duration).audio

    out = ffmpeg.output(
        video,
        audio,
        filename=f"{id}.{save_filetype}",
        loglevel="error"
    )

    # download the video
    out.overwrite_output().run()


def play_video(filename):
    mp4 = open(filename,'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    return HTML('''
    <video width=400 controls>
        <source src="{data_url}" type="video/mp4">
    </video>
    '''.format(data_url=data_url))


In [5]:
# @markdown Indicate the save_location. Make sure to add a ".mp4" or ".mkv" in the end, you can add folder names too.
youtube_url = "https://www.youtube.com/watch?v=9CTzhqVHmww" #@param {type:"string"}
timestamp = "00:27-00:38" #@param {type:"string"}
save_filetype = "mp4"  #@param {type: "string"}

#@markdown # NOTE
#@markdown Timestamps should follow this format `0:39-1:10`

'''
markdown/input ends here.
'''

# preprocess data
video_url, id = get_youtube_url(youtube_url, "video")
audio_url = get_youtube_url(youtube_url, "audio")
start_time, duration = get_duration_in_seconds(timestamp)


print(f"started downloading clip id: {id}.")
download_video(video_url, audio_url, start_time, duration)
print(f"finished downloading clip id: {id}.")

started downloading clip id: 9CTzhqVHmww.
finished downloading clip id: 9CTzhqVHmww.


In [6]:
play_video("9CTzhqVHmww.mp4")